## Best practices for releases

This notebook is a walkthrough of the Cytoscape Release build process. Use the BUILD_PARENT_DIR variable to specify a directory to build cytoscape in.

#### NOTE: Make sure BUILD_PARENT_DIR is in `.gitignore`

1. Update versions
1. Update Core apps to use new API
1. Build Installers
1. Test on different OSs
1. Deploy subrepos to nexus
1. Post the installers to http://github.com/cytoscape/cytoscape/releases
1. Deploy updated core apps

After release:
1. Merge the branch used to build installers into master and tag the release
1. If master release, update the version in dev branch
1. Update Cytoscape manual via https://github.com/cytoscape/cytoscape-manual
1. Update www.github.com/cytoscape/cytoscape.github.com (downloads page, roadmap, etc.)
1. Update system requirements script at https://github.com/cytoscape/cytoscape-admin-scripts/tree/master/system-checker


In [29]:
from subprocess import Popen, PIPE
import os
import shutil

NOTEBOOK_DIR = os.path.join(os.getcwd());

%env JAVA_HOME=/usr/lib/jvm/java-1.8.0-openjdk
!echo $JAVA_HOME

env: JAVA_HOME=/usr/lib/jvm/java-1.8.0-openjdk
/usr/lib/jvm/java-1.8.0-openjdk


In [2]:
os.chdir(NOTEBOOK_DIR)

# Point to build location (the directory to clone parent cytoscape into)
BUILD_PARENT_DIR = os.path.join(os.getcwd(), 'build_3.7.2')
if not os.path.exists(BUILD_PARENT_DIR):
    os.mkdir(BUILD_PARENT_DIR)
else:
    shutil.rmtree(BUILD_PARENT_DIR)
    os.mkdir(BUILD_PARENT_DIR)

os.chdir(BUILD_PARENT_DIR)
![[ -d cytoscape ]] || git clone https://github.com/cytoscape/cytoscape
CYTOSCAPE_ROOT_DIR = os.path.join(BUILD_PARENT_DIR, 'cytoscape')
CYTOSCAPE_DIR = os.path.join(CYTOSCAPE_ROOT_DIR, 'cytoscape')

def cd(directory=BUILD_PARENT_DIR, *subdirs):
    if subdirs:
        directory = os.path.join(directory, *subdirs)
    if os.getcwd() != directory:
        os.chdir(directory)

Cloning into 'cytoscape'...
remote: Enumerating objects: 1, done.
remote: Counting objects: 100% (1/1), done.
remote: Total 530 (delta 0), reused 1 (delta 0), pack-reused 529
Receiving objects: 100% (530/530), 142.35 KiB | 0 bytes/s, done.
Resolving deltas: 100% (253/253), done.


In [3]:
STARTING_BRANCH = 'release/3.7.1'     # develop for major release, release/3.X.X for minor release
NEW_BRANCH = 'release/3.7.2'    # branch to create that will be deployed
OLD_VERSION = '3.7.1'  # Version to replace in maven files
NEW_VERSION = '3.7.2'           # New version to set across maven
OLD_RELEASE_VERSION = '3.7.1'   # Release Version to replace on website/version checker

## 1. Pull the develop branch of Cytoscape

In [4]:
cd(CYTOSCAPE_ROOT_DIR)
![[ -d cytoscape ]] || ./cy.sh init
cd(CYTOSCAPE_DIR)
!./cy.sh run-all "git checkout {STARTING_BRANCH}"

Target directory = 
Cytoscape project will be cloned to: /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape
Cloning into 'cytoscape'...
remote: Enumerating objects: 1, done.
remote: Counting objects: 100% (1/1), done.
remote: Total 530 (delta 0), reused 1 (delta 0), pack-reused 529
Receiving objects: 100% (530/530), 142.35 KiB | 0 bytes/s, done.
Resolving deltas: 100% (253/253), done.
Cloning: parent (URI = git@github.com:cytoscape/cytoscape-parent.git)
Cloning into 'parent'...
remote: Enumerating objects: 32, done.
remote: Counting objects: 100% (32/32), done.
remote: Compressing objects: 100% (31/31), done.
remote: Total 1601 (delta 16), reused 16 (delta 1), pack-reused 1569
Receiving objects: 100% (1601/1601), 251.22 KiB | 0 bytes/s, done.
Resolving deltas: 100% (601/601), done.
~/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/parent ~/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape
Already on 'develop'
~/cytoscape-admin-scripts/build_3.7.2/cytoscape/cyto

## 1a. Reset

In [5]:
cd(CYTOSCAPE_DIR)
!./cy.sh run-all 'git clean -f -d'
!./cy.sh run-all 'git reset --hard'

------------------------------------------------------------------------
Executing command: git clean -f -d
--in .
------------------------------------------------------------------------
--in parent
------------------------------------------------------------------------
--in api
------------------------------------------------------------------------
--in impl
------------------------------------------------------------------------
--in support
------------------------------------------------------------------------
--in gui-distribution
------------------------------------------------------------------------
--in app-developer
------------------------------------------------------------------------
------------------------------------------------------------------------
Executing command: git reset --hard
--in .
HEAD is now at a3e5e65 Updated run-all command
------------------------------------------------------------------------
--in parent
HEAD is now at 69b7444 Switch\ to\ 3.7.1


## 2. Create new branch locally

In [6]:
cd(CYTOSCAPE_DIR)
!./cy.sh run-all 'git checkout -b {NEW_BRANCH}'
# !./cy.sh run-all 'git pull' # only necessary if branch is pushed

------------------------------------------------------------------------
Executing command: git checkout -b release/3.7.2
--in .
Switched to a new branch 'release/3.7.2'
------------------------------------------------------------------------
--in parent
Switched to a new branch 'release/3.7.2'
------------------------------------------------------------------------
--in api
Switched to a new branch 'release/3.7.2'
------------------------------------------------------------------------
--in impl
Switched to a new branch 'release/3.7.2'
------------------------------------------------------------------------
--in support
Switched to a new branch 'release/3.7.2'
------------------------------------------------------------------------
--in gui-distribution
Switched to a new branch 'release/3.7.2'
------------------------------------------------------------------------
--in app-developer
Switched to a new branch 'release/3.7.2'
-------------------------------------------------------------

In [7]:
cd(CYTOSCAPE_DIR)
!./cy.sh run-all 'git status'

------------------------------------------------------------------------
Executing command: git status
--in .
# On branch release/3.7.2
nothing to commit, working directory clean
------------------------------------------------------------------------
--in parent
# On branch release/3.7.2
nothing to commit, working directory clean
------------------------------------------------------------------------
--in api
# On branch release/3.7.2
nothing to commit, working directory clean
------------------------------------------------------------------------
--in impl
# On branch release/3.7.2
nothing to commit, working directory clean
------------------------------------------------------------------------
--in support
# On branch release/3.7.2
nothing to commit, working directory clean
------------------------------------------------------------------------
--in gui-distribution
# On branch release/3.7.2
nothing to commit, working directory clean
---------------------------------------------

## 3. Update versions in pom files and all documents

In [8]:
cd(CYTOSCAPE_DIR)
!mvn versions:set -DnewVersion={NEW_VERSION}

[INFO] Scanning for projects...
[WARNING] 
[WARNING] Some problems were encountered while building the effective model for org.cytoscape:app-api:bundle:3.7.1
[WARNING] 'dependencies.dependency.(groupId:artifactId:type:classifier)' must be unique: org.cytoscape:jobs-api:jar -> duplicate declaration of version ${project.version} @ line 180, column 15
[WARNING] 
[WARNING] It is highly recommended to fix these problems because they threaten the stability of your build.
[WARNING] 
[WARNING] For this reason, future Maven versions might no longer support building such malformed projects.
[WARNING] 
[INFO] ------------------------------------------------------------------------
[INFO] Reactor Build Order:
[INFO] 
[INFO] Basic Cytoscape POM Configuration
[INFO] Cytoscape API Parent Project POM
[INFO] Cytoscape Documentation Taglets
[INFO] Cytoscape Event API (event-api)
[INFO] Cytoscape Model API (model-api)
[INFO] Cytoscape Service API (service-api)
[INFO] Cytoscape View Model API (viewmodel-a

[INFO] Final Memory: 35M/429M
[INFO] ------------------------------------------------------------------------


In [9]:
# then update the versions in the parent directory
cd(CYTOSCAPE_DIR, 'parent')
!mvn versions:set -DnewVersion={NEW_VERSION}

[INFO] Scanning for projects...
[INFO]                                                                         
[INFO] ------------------------------------------------------------------------
[INFO] Building Basic Cytoscape POM Configuration 3.7.1
[INFO] ------------------------------------------------------------------------
[INFO] 
[INFO] --- versions-maven-plugin:2.7:set (default-cli) @ parent ---
[INFO] Searching for local aggregator root...
[INFO] Local aggregation root: /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape
[INFO] Processing change of org.cytoscape:parent:3.7.1 -> 3.7.2
[INFO] Processing org.cytoscape:parent
[INFO]     Updating project org.cytoscape:parent
[INFO]         from version 3.7.1 to 3.7.2
[INFO] 
[INFO] Processing org.cytoscape.app-developer:cytoscape
[INFO]     Updating parent org.cytoscape:parent
[INFO]         from version 3.7.1 to 3.7.2
[INFO]     Updating project org.cytoscape.app-developer:cytoscape
[INFO]         from version 3.7

[INFO] 
[INFO] Processing org.cytoscape:filter-impl
[INFO]     Updating parent org.cytoscape:impl-parent
[INFO]         from version 3.7.1 to 3.7.2
[INFO]     Updating project org.cytoscape:filter-impl
[INFO]         from version 3.7.1 to 3.7.2
[INFO] 
[INFO] Processing org.cytoscape:filter2-impl
[INFO]     Updating parent org.cytoscape:impl-parent
[INFO]         from version 3.7.1 to 3.7.2
[INFO] 
[INFO] Processing org.cytoscape:graphml-impl
[INFO]     Updating parent org.cytoscape:impl-parent
[INFO]         from version 3.7.1 to 3.7.2
[INFO] 
[INFO] Processing org.cytoscape:group-api
[INFO]     Updating parent org.cytoscape:api-parent
[INFO]         from version 3.7.1 to 3.7.2
[INFO] 
[INFO] Processing org.cytoscape:group-impl
[INFO]     Updating parent org.cytoscape:impl-parent
[INFO]         from version 3.7.1 to 3.7.2
[INFO]     Updating project org.cytoscape:group-impl
[INFO]         from version 3.7.1 to 3.7.2
[INFO] 
[INFO] Processing org.cytoscape:gui-cmdline-parser-impl
[INFO

[INFO]     Updating project org.cytoscape:taglets
[INFO]         from version 3.7.1 to 3.7.2
[INFO] 
[INFO] Processing org.cytoscape:task-testing-impl
[INFO]     Updating parent org.cytoscape:support-parent
[INFO]         from version 3.7.1 to 3.7.2
[INFO]     Updating project org.cytoscape:task-testing-impl
[INFO]         from version 3.7.1 to 3.7.2
[INFO] 
[INFO] Processing org.cytoscape:util-api
[INFO]     Updating parent org.cytoscape:api-parent
[INFO]         from version 3.7.1 to 3.7.2
[INFO] 
[INFO] Processing org.cytoscape:util-impl
[INFO]     Updating parent org.cytoscape:impl-parent
[INFO]         from version 3.7.1 to 3.7.2
[INFO]     Updating project org.cytoscape:util-impl
[INFO]         from version 3.7.1 to 3.7.2
[INFO] 
[INFO] Processing org.cytoscape:viewmodel-api
[INFO]     Updating parent org.cytoscape:api-parent
[INFO]         from version 3.7.1 to 3.7.2
[INFO] 
[INFO] Processing org.cytoscape:viewmodel-impl-parent
[INFO]     Updating parent org.cytoscape:impl-paren

## 3a. Commit (or reset) versions in pom files

In [10]:
cd(CYTOSCAPE_DIR)
#!mvn version:revert
!mvn versions:commit

cd(CYTOSCAPE_DIR, 'parent')
#!mvn version:revert
!mvn versions:commit

[INFO] Scanning for projects...
[WARNING] 
[WARNING] Some problems were encountered while building the effective model for org.cytoscape:app-api:bundle:3.7.2
[WARNING] 'dependencies.dependency.(groupId:artifactId:type:classifier)' must be unique: org.cytoscape:jobs-api:jar -> duplicate declaration of version ${project.version} @ line 180, column 15
[WARNING] 
[WARNING] It is highly recommended to fix these problems because they threaten the stability of your build.
[WARNING] 
[WARNING] For this reason, future Maven versions might no longer support building such malformed projects.
[WARNING] 
[INFO] ------------------------------------------------------------------------
[INFO] Reactor Build Order:
[INFO] 
[INFO] Basic Cytoscape POM Configuration
[INFO] Cytoscape API Parent Project POM
[INFO] Cytoscape Documentation Taglets
[INFO] Cytoscape Event API (event-api)
[INFO] Cytoscape Model API (model-api)
[INFO] Cytoscape Service API (service-api)
[INFO] Cytoscape View Model API (viewmodel-a

[INFO] 
[INFO] --- versions-maven-plugin:2.7:commit (default-cli) @ event-api ---
[INFO] Accepting all changes to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/api/event-api/pom.xml
[INFO]                                                                         
[INFO] ------------------------------------------------------------------------
[INFO] Building Cytoscape Model API (model-api) 3.7.2
[INFO] ------------------------------------------------------------------------
[INFO] 
[INFO] --- versions-maven-plugin:2.7:commit (default-cli) @ model-api ---
[INFO] Accepting all changes to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/api/model-api/pom.xml
[INFO]                                                                         
[INFO] ------------------------------------------------------------------------
[INFO] Building Cytoscape Service API (service-api) 3.7.2
[INFO] -----------------------------------------------------------------

[INFO] 
[INFO] --- versions-maven-plugin:2.7:commit (default-cli) @ app-api ---
[INFO] Accepting all changes to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/api/app-api/pom.xml
[INFO]                                                                         
[INFO] ------------------------------------------------------------------------
[INFO] Building Cytoscape Work Swing API (work-swing-api) 3.7.2
[INFO] ------------------------------------------------------------------------
[INFO] 
[INFO] --- versions-maven-plugin:2.7:commit (default-cli) @ work-swing-api ---
[INFO] Accepting all changes to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/api/work-swing-api/pom.xml
[INFO]                                                                         
[INFO] ------------------------------------------------------------------------
[INFO] Building Cytoscape Swing Utility API (swing-util-api) 3.7.2
[INFO] ----------------------------------------

[INFO]                                                                         
[INFO] ------------------------------------------------------------------------
[INFO] Building Cytoscape IO Impl (io-impl) 3.7.2
[INFO] ------------------------------------------------------------------------
[WARNING] The POM for org.eclipse.m2e:lifecycle-mapping:jar:1.0.0 is missing, no dependency information available
[WARNING] Failed to retrieve plugin descriptor for org.eclipse.m2e:lifecycle-mapping:1.0.0: Plugin org.eclipse.m2e:lifecycle-mapping:1.0.0 or one of its dependencies could not be resolved: Failed to read artifact descriptor for org.eclipse.m2e:lifecycle-mapping:jar:1.0.0
[INFO] 
[INFO] --- versions-maven-plugin:2.7:commit (default-cli) @ io-impl ---
[INFO] Accepting all changes to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/impl/io-impl/impl/pom.xml
[INFO]                                                                         
[INFO] ---------------------------

[INFO]                                                                         
[INFO] ------------------------------------------------------------------------
[INFO] Building Cytoscape Property Impl (property-impl) 3.7.2
[INFO] ------------------------------------------------------------------------
[WARNING] The POM for org.eclipse.m2e:lifecycle-mapping:jar:1.0.0 is missing, no dependency information available
[WARNING] Failed to retrieve plugin descriptor for org.eclipse.m2e:lifecycle-mapping:1.0.0: Plugin org.eclipse.m2e:lifecycle-mapping:1.0.0 or one of its dependencies could not be resolved: Failed to read artifact descriptor for org.eclipse.m2e:lifecycle-mapping:jar:1.0.0
[INFO] 
[INFO] --- versions-maven-plugin:2.7:commit (default-cli) @ property-impl ---
[INFO] Accepting all changes to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/impl/property-impl/pom.xml
[INFO]                                                                         
[INFO] --------

[INFO] Accepting all changes to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/impl/application-impl/pom.xml
[INFO]                                                                         
[INFO] ------------------------------------------------------------------------
[INFO] Building Cytoscape Datasource Impl (datasource-impl) 3.7.2
[INFO] ------------------------------------------------------------------------
[WARNING] The POM for org.eclipse.m2e:lifecycle-mapping:jar:1.0.0 is missing, no dependency information available
[WARNING] Failed to retrieve plugin descriptor for org.eclipse.m2e:lifecycle-mapping:1.0.0: Plugin org.eclipse.m2e:lifecycle-mapping:1.0.0 or one of its dependencies could not be resolved: Failed to read artifact descriptor for org.eclipse.m2e:lifecycle-mapping:jar:1.0.0
[INFO] 
[INFO] --- versions-maven-plugin:2.7:commit (default-cli) @ datasource-impl ---
[INFO] Accepting all changes to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cy

[INFO] Accepting all changes to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/support/archetypes/pom.xml
[INFO]                                                                         
[INFO] ------------------------------------------------------------------------
[INFO] Building Cytoscape 3 Archetype - Creates an App providing public API 3.7.2
[INFO] ------------------------------------------------------------------------
[INFO] 
[INFO] --- versions-maven-plugin:2.7:commit (default-cli) @ api-provider-app ---
[INFO] Accepting all changes to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/support/archetypes/api-provider-app/pom.xml
[INFO]                                                                         
[INFO] ------------------------------------------------------------------------
[INFO] Building Cytoscape 3 Archetype - Creates an App with a Task 3.7.2
[INFO] ----------------------------------------------------------------------

[INFO] 
[INFO] --- versions-maven-plugin:2.7:commit (default-cli) @ branding ---
[INFO] Accepting all changes to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/gui-distribution/branding/pom.xml
[INFO]                                                                         
[INFO] ------------------------------------------------------------------------
[INFO] Building Cytoscape Application Implementation Metadata 3.7.2
[INFO] ------------------------------------------------------------------------
[INFO] 
[INFO] --- versions-maven-plugin:2.7:commit (default-cli) @ application-metadata-impl ---
[INFO] Accepting all changes to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/gui-distribution/application-metadata-impl/pom.xml
[INFO]                                                                         
[INFO] ------------------------------------------------------------------------
[INFO] Building Cytoscape GUI-Distribution Integration Test 

[INFO] Final Memory: 51M/694M
[INFO] ------------------------------------------------------------------------
[INFO] Scanning for projects...
[INFO]                                                                         
[INFO] ------------------------------------------------------------------------
[INFO] Building Basic Cytoscape POM Configuration 3.7.2
[INFO] ------------------------------------------------------------------------
[INFO] 
[INFO] --- versions-maven-plugin:2.7:commit (default-cli) @ parent ---
[INFO] ------------------------------------------------------------------------
[INFO] BUILD SUCCESS
[INFO] ------------------------------------------------------------------------
[INFO] Total time: 0.798s
[INFO] Finished at: Tue Sep 03 15:23:07 PDT 2019
[INFO] Final Memory: 15M/303M
[INFO] ------------------------------------------------------------------------


## 3b. Update version in other files (poms, executables)

In [11]:
%%bash -s "$OLD_VERSION" "$NEW_VERSION" "$CYTOSCAPE_DIR"

cd "$3"

echo "* Updating version numbers in pom files..."
find . -name "pom.xml" -type f -print0 | xargs -0 sed -i "s|$1|$2|g"
echo "Done"

* Updating version numbers in pom files...
Done


In [12]:
%%bash -s "$OLD_VERSION" "$NEW_VERSION" "$CYTOSCAPE_DIR"

cd "$3/gui-distribution/assembly/src/main/bin/"

echo "* Updating version numbers in executables..."
find . -name "cytoscape.*" -type f -print0 | xargs -0 sed -i "s/$1/$2/g"
echo "Done"

* Updating version numbers in executables...
Done


In [13]:
%%bash -s "$OLD_RELEASE_VERSION" "$NEW_VERSION" "$CYTOSCAPE_DIR"

cd "$3/impl/core-task-impl/src/main/java/org/cytoscape/task/internal/help"

echo "* Updating Manual link"
find . -name "HelpTaskFactory.jav*" -type f -print0 | xargs -0 sed -i "s|$1|$2|g"
echo "Done"

* Updating Manual link
Done


## 3c. Maven clean and check for outstanding occurrences of old version

In [14]:
!echo "* Cleaning old installers"
cd(CYTOSCAPE_DIR, 'gui-distribution', 'packaging')
!mvn clean -q
cd(CYTOSCAPE_DIR, 'gui-distribution', 'splash-launcher')
!mvn clean -q
!echo "Done"

* Cleaning old installers
Done


In [15]:
cd(CYTOSCAPE_DIR)
ESCAPED = OLD_VERSION.replace('.', '\\.')
!echo "* Showing occurrences of {ESCAPED} in `pwd`:" && grep -ri '{ESCAPED}' .

* Showing occurrences of 3\.7\.1 in /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape:
./.git/config:[branch "release/3.7.1"]
./.git/config:	merge = refs/heads/release/3.7.1
./.git/packed-refs:a3e5e65497a0e868429146df1a709ab5595f7f1f refs/remotes/origin/release/3.7.1
./.git/packed-refs:a3e5e65497a0e868429146df1a709ab5595f7f1f refs/tags/3.7.1
./.git/logs/refs/heads/release/3.7.1:0000000000000000000000000000000000000000 a3e5e65497a0e868429146df1a709ab5595f7f1f David Otasek <dotasek.dev@gmail.com> 1567549323 -0700	branch: Created from refs/remotes/origin/release/3.7.1
./.git/logs/HEAD:8d3c88ce7ba8d1daae921fe1c144dbdd2c7e94ee a3e5e65497a0e868429146df1a709ab5595f7f1f David Otasek <dotasek.dev@gmail.com> 1567549323 -0700	checkout: moving from develop to release/3.7.1
./.git/logs/HEAD:a3e5e65497a0e868429146df1a709ab5595f7f1f a3e5e65497a0e868429146df1a709ab5595f7f1f David Otasek <dotasek.dev@gmail.com> 1567549333 -0700	checkout: moving from release/3.7.1 to release/3.7.2


./gui-distribution/.git/packed-refs:c01c53ff55f0c9a971656b3bf161739d930d3df2 refs/remotes/origin/release/3.7.1
./gui-distribution/.git/packed-refs:7c98d2c2a2d760f464566b7e66201a480c6cd3c6 refs/tags/3.7.1
./gui-distribution/.git/logs/refs/heads/release/3.7.1:0000000000000000000000000000000000000000 c01c53ff55f0c9a971656b3bf161739d930d3df2 David Otasek <dotasek.dev@gmail.com> 1567549323 -0700	branch: Created from refs/remotes/origin/release/3.7.1
./gui-distribution/.git/logs/HEAD:673316dfb89311c0c457ada055cc8502d911d417 c01c53ff55f0c9a971656b3bf161739d930d3df2 David Otasek <dotasek.dev@gmail.com> 1567549323 -0700	checkout: moving from develop to release/3.7.1
./gui-distribution/.git/logs/HEAD:c01c53ff55f0c9a971656b3bf161739d930d3df2 c01c53ff55f0c9a971656b3bf161739d930d3df2 David Otasek <dotasek.dev@gmail.com> 1567549333 -0700	checkout: moving from release/3.7.1 to release/3.7.2
./app-developer/.git/config:[branch "release/3.7.1"]
./app-developer/.git/config:	merge = refs/heads/release/3.

In [16]:
cd(CYTOSCAPE_DIR)
ESCAPED = OLD_RELEASE_VERSION.replace('.', '\\.')
!echo "* Showing occurrences of {ESCAPED} in `pwd`:" && grep -ri '{ESCAPED}' .

* Showing occurrences of 3\.7\.1 in /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape:
./.git/config:[branch "release/3.7.1"]
./.git/config:	merge = refs/heads/release/3.7.1
./.git/packed-refs:a3e5e65497a0e868429146df1a709ab5595f7f1f refs/remotes/origin/release/3.7.1
./.git/packed-refs:a3e5e65497a0e868429146df1a709ab5595f7f1f refs/tags/3.7.1
./.git/logs/refs/heads/release/3.7.1:0000000000000000000000000000000000000000 a3e5e65497a0e868429146df1a709ab5595f7f1f David Otasek <dotasek.dev@gmail.com> 1567549323 -0700	branch: Created from refs/remotes/origin/release/3.7.1
./.git/logs/HEAD:8d3c88ce7ba8d1daae921fe1c144dbdd2c7e94ee a3e5e65497a0e868429146df1a709ab5595f7f1f David Otasek <dotasek.dev@gmail.com> 1567549323 -0700	checkout: moving from develop to release/3.7.1
./.git/logs/HEAD:a3e5e65497a0e868429146df1a709ab5595f7f1f a3e5e65497a0e868429146df1a709ab5595f7f1f David Otasek <dotasek.dev@gmail.com> 1567549333 -0700	checkout: moving from release/3.7.1 to release/3.7.2


./app-developer/.git/config:[branch "release/3.7.1"]
./app-developer/.git/config:	merge = refs/heads/release/3.7.1
./app-developer/.git/packed-refs:1bd9c12a5a07db5471bba4017f33c9aba2b86941 refs/remotes/origin/release/3.7.1
./app-developer/.git/logs/refs/heads/release/3.7.1:0000000000000000000000000000000000000000 1bd9c12a5a07db5471bba4017f33c9aba2b86941 David Otasek <dotasek.dev@gmail.com> 1567549323 -0700	branch: Created from refs/remotes/origin/release/3.7.1
./app-developer/.git/logs/HEAD:652de74c68c423a875113cc5217cb21a4453ed53 1bd9c12a5a07db5471bba4017f33c9aba2b86941 David Otasek <dotasek.dev@gmail.com> 1567549323 -0700	checkout: moving from develop to release/3.7.1
./app-developer/.git/logs/HEAD:1bd9c12a5a07db5471bba4017f33c9aba2b86941 1bd9c12a5a07db5471bba4017f33c9aba2b86941 David Otasek <dotasek.dev@gmail.com> 1567549333 -0700	checkout: moving from release/3.7.1 to release/3.7.2


## 4. Build Cytoscape and ensure no errors
This may take a while. Expect to build subrepos first before building from the root directory

In [17]:
cd(CYTOSCAPE_DIR)
with open('build_output.txt', 'w') as outf:
    process = Popen('mvn -fae clean install -Dmaven.test.skip=true'.split(' '), 
                stdout=outf,
                cwd=CYTOSCAPE_DIR)
    process.wait()

print("Showing ERROR lines in build...")
!cat build_output.txt | grep ERROR

Showing ERROR lines in build...


## 5. Commit changes to new branch

In [18]:
# if successful, commit the changes
cd(CYTOSCAPE_DIR)
!./cy.sh run-all 'git add .'
!./cy.sh run-all 'git commit -m "Update version to {NEW_VERSION}"'

------------------------------------------------------------------------
Executing command: git add .
--in .
------------------------------------------------------------------------
--in parent
------------------------------------------------------------------------
--in api
------------------------------------------------------------------------
--in impl
------------------------------------------------------------------------
--in support
------------------------------------------------------------------------
--in gui-distribution
------------------------------------------------------------------------
--in app-developer
------------------------------------------------------------------------
------------------------------------------------------------------------
Executing command: git commit -m "Update version to 3.7.2"
--in .
[release/3.7.2 1e7d694] Update version to 3.7.2
 2 files changed, 50468 insertions(+), 1 deletion(-)
 create mode 100644 build_output.txt
------------------

In [19]:
cd(CYTOSCAPE_DIR)
!./cy.sh status

------------------------------------------------------------------------
- .:

# On branch release/3.7.2
nothing to commit, working directory clean
------------------------------------------------------------------------
- parent:

# On branch release/3.7.2
nothing to commit, working directory clean
------------------------------------------------------------------------
- api:

# On branch release/3.7.2
nothing to commit, working directory clean
------------------------------------------------------------------------
- impl:

# On branch release/3.7.2
nothing to commit, working directory clean
------------------------------------------------------------------------
- support:

# On branch release/3.7.2
nothing to commit, working directory clean
------------------------------------------------------------------------
- gui-distribution:

# On branch release/3.7.2
nothing to commit, working directory clean
------------------------------------------------------------------------
- app-de

## 6. Build Cytoscape installers
This requires Install4J to be configured on your machine via the instructions at the Cytoscape README

In [20]:
cd(CYTOSCAPE_DIR, 'gui-distribution', 'packaging')
%env MAC_KEYSTORE_PASSWORD=
!mvn clean install -U

env: MAC_KEYSTORE_PASSWORD=
[INFO] Scanning for projects...
[WARNING] 
[WARNING] Some problems were encountered while building the effective model for org.cytoscape.distribution:packaging:jar:3.7.2
[WARNING] 'build.plugins.plugin.version' for org.sonatype.install4j:install4j-maven-plugin is missing. @ line 104, column 15
[WARNING] 
[WARNING] It is highly recommended to fix these problems because they threaten the stability of your build.
[WARNING] 
[WARNING] For this reason, future Maven versions might no longer support building such malformed projects.
[WARNING] 
[INFO]                                                                         
[INFO] ------------------------------------------------------------------------
[INFO] Building Cytoscape Release Packaging 3.7.2
[INFO] ------------------------------------------------------------------------
Downloading: https://repo.maven.apache.org/maven2/org/sonatype/install4j/install4j-maven-plugin/maven-metadata.xml
Downloading: http://code

[INFO] 
[INFO] Compressed media file 'Mac OS X':
[INFO]   Compressing files
[INFO]   Generating VM options file vmoptions.txt.
[INFO]   Signing installer
[INFO]   Signing DMG
[INFO]   Moving media files to media directory /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/gui-distribution/packaging/target/media
[INFO]   The name of the media file is Cytoscape_3_7_2_macos.dmg.
[INFO]   The size of the media file is 168.1 MB
[INFO]   
[INFO]   Important: Please make sure that the file
[INFO]       /home/cybuilder/.install4j7/jres/macosx-amd64-1.8.0_162.tar.gz
[INFO]   can be downloaded from
[INFO]       http://chianti.ucsd.edu/jres/macosx-amd64-1.8.0_162.tar.gz
[INFO] Writing md5sums.
[INFO] Writing updates.xml.
[INFO] Build completed in 25.3 seconds.
[INFO] 
[INFO] --- maven-install-plugin:2.3.1:install (default-install) @ packaging ---
[INFO] Installing /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/gui-distribution/packaging/target/packagi

- Update core apps to rely on deployed releases, test
- Deploy and push them to app store
- Merge develop into master branch
- Tag and release master, publish release
- Change dev branch version

## 7. Deploy JARs to Nexus

- Need to have our repository properly configured in ~/.m2/settings.xml
- Cytoscape Project POM will fail. This is expected

In [22]:
cd(CYTOSCAPE_DIR)
!mvn clean deploy -Dmaven.test.skip=true

[INFO] Scanning for projects...
[WARNING] 
[WARNING] Some problems were encountered while building the effective model for org.cytoscape:app-api:bundle:3.7.2
[WARNING] 'dependencies.dependency.(groupId:artifactId:type:classifier)' must be unique: org.cytoscape:jobs-api:jar -> duplicate declaration of version ${project.version} @ line 180, column 15
[WARNING] 
[WARNING] It is highly recommended to fix these problems because they threaten the stability of your build.
[WARNING] 
[WARNING] For this reason, future Maven versions might no longer support building such malformed projects.
[WARNING] 
[INFO] ------------------------------------------------------------------------
[INFO] Reactor Build Order:
[INFO] 
[INFO] Basic Cytoscape POM Configuration
[INFO] Cytoscape API Parent Project POM
[INFO] Cytoscape Documentation Taglets
[INFO] Cytoscape Event API (event-api)
[INFO] Cytoscape Model API (model-api)
[INFO] Cytoscape Service API (service-api)
[INFO] Cytoscape View Model API (viewmodel-a

[INFO] 
[INFO] --- maven-clean-plugin:2.4.1:clean (default-clean) @ api-parent ---
[INFO] Deleting /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/api/target
[INFO] 
[INFO] >>> maven-source-plugin:2.4:jar (attach-sources) @ api-parent >>>
[INFO] 
[INFO] <<< maven-source-plugin:2.4:jar (attach-sources) @ api-parent <<<
[INFO] 
[INFO] --- maven-source-plugin:2.4:jar (attach-sources) @ api-parent ---
[INFO] 
[INFO] >>> maven-source-plugin:2.4:aggregate (aggregate-source) @ api-parent >>>
[INFO]                                                                         
[INFO] >>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>
[INFO] Forking Cytoscape Property API (property-api) 3.7.2
[INFO] >>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>
[INFO] 
[INFO] --- maven-jaxb2-plugin:0.8.1:generate (bookmarks) @ property-api ---
[INFO] Started execution.
[INFO] JAXB API is loaded from the [jar:file:/usr/lib/jvm/java-1.8.0-openjdk-

[INFO]                                                                         
[INFO] >>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>
[INFO] Forking Cytoscape Feature Repository 3.7.2
[INFO] >>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>
[INFO] 
[INFO] --- maven-resources-plugin:2.6:copy-resources (copy-resources) @ features ---
[INFO] Using 'UTF-8' encoding to copy filtered resources.
[INFO] Copying 1 resource
[INFO] 
[INFO] <<< maven-source-plugin:2.4:aggregate (aggregate-source) @ api-parent <<<
[INFO] 
[INFO] --- maven-source-plugin:2.4:aggregate (aggregate-source) @ api-parent ---
[INFO] Building jar: /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/api/target/api-parent-3.7.2-sources.jar
[INFO] 
[INFO] --- maven-install-plugin:2.3.1:install (default-install) @ api-parent ---
[INFO] Installing /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/api/pom.xml to /home/cybuilder/.m2/reposito

[INFO] episodeFile:/home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/impl/io-impl/impl/target/generated-sources/xjc/vizmap/META-INF/sun-jaxb.episode
[INFO] episode:true
[INFO] classpathElements:[/home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/impl/io-impl/impl/target/classes]
[INFO] plugins:null
[INFO] episodes:null
[INFO] useDependenciesAsEpisodes:false
[INFO] xjcPlugins:null
[INFO] episodes:null
[INFO] schemaFiles (calculated):[/home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/impl/io-impl/impl/src/main/resources/xsd/vizmap.xsd]
[INFO] bindingFiles (calculated):[]
[INFO] xjcPluginArtifacts (resolved):[]
[INFO] xjcPluginFiles (resolved):[]
[INFO] xjcPluginURLs (resolved):[]
[INFO] episodeArtifacts (resolved):[]
[INFO] episodeFiles (resolved):[]
[INFO] optionsConfiguration:OptionsConfiguration [specVersion=2.1
 generateDirectory=/home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/impl/io-impl/impl/t

Uploaded: http://code.cytoscape.org/nexus/content/repositories/releases/org/cytoscape/taglets/3.7.2/taglets-3.7.2.jar (12 KB at 20.3 KB/sec)
Uploading: http://code.cytoscape.org/nexus/content/repositories/releases/org/cytoscape/taglets/3.7.2/taglets-3.7.2.pom
Uploaded: http://code.cytoscape.org/nexus/content/repositories/releases/org/cytoscape/taglets/3.7.2/taglets-3.7.2.pom (4 KB at 7.5 KB/sec)
Downloading: http://code.cytoscape.org/nexus/content/repositories/releases/org/cytoscape/taglets/maven-metadata.xml
Downloaded: http://code.cytoscape.org/nexus/content/repositories/releases/org/cytoscape/taglets/maven-metadata.xml (2 KB at 4.0 KB/sec)
Uploading: http://code.cytoscape.org/nexus/content/repositories/releases/org/cytoscape/taglets/maven-metadata.xml
Uploaded: http://code.cytoscape.org/nexus/content/repositories/releases/org/cytoscape/taglets/maven-metadata.xml (2 KB at 2.4 KB/sec)
Uploading: http://code.cytoscape.org/nexus/content/repositories/releases/org/cytoscape/taglets/3.7.2/

...

[INFO] Copying artifact: javax.annotation:javax.annotation-api:jar:1.2
[INFO] Copying artifact: org.apache.geronimo.specs:geronimo-jaspic_1.0_spec:jar:1.1
[INFO] Copying artifact: org.ow2.asm:asm:jar:6.2
[INFO] Copying artifact: org.ow2.asm:asm-util:jar:6.2
[INFO] Copying artifact: org.ow2.asm:asm-tree:jar:6.2
[INFO] Copying artifact: org.ow2.asm:asm-analysis:jar:6.2
[INFO] Copying artifact: org.ow2.asm:asm-commons:jar:6.2
[INFO] Copying artifact: org.apache.aries.spifly:org.apache.aries.spifly.dynamic.bundle:jar:1.0.10
[INFO] Copying artifact: org.apache.aries:org.apache.aries.util:jar:1.1.3
[INFO] Copying artifact: org.eclipse.jetty:jetty-continuation:jar:9.4.10.v20180503
[INFO] Copying artifact: org.eclipse.jetty:jetty-http:jar:9.4.10.v20180503
[INFO] Copying artifact: org.eclipse.jetty:jetty-io:jar:9.4.10.v20180503
[INFO] Copying artifact: org.eclipse.jetty:jetty-jaspi:jar:9.4.10.v20180503
[INFO] Copying artifact: org.eclipse.jetty:jetty-plus:jar:9.4.10.v20180503
[INFO] Copying art

[INFO] Copying opencl-cycl-3.5.0.jar to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/gui-distribution/assembly/target/dependencies/apps/opencl-cycl-3.5.0.jar
[INFO] Copying opencl-layout-3.5.0.jar to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/gui-distribution/assembly/target/dependencies/apps/opencl-layout-3.5.0.jar
[INFO] Copying welcome-3.5.3.jar to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/gui-distribution/assembly/target/dependencies/apps/welcome-3.5.3.jar
[INFO] Copying diffusion-1.5.4.jar to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/gui-distribution/assembly/target/dependencies/apps/diffusion-1.5.4.jar
[INFO] Copying copycatLayout-1.2.3.jar to /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/gui-distribution/assembly/target/dependencies/apps/copycatLayout-1.2.3.jar
[INFO] Copying cyBrowser-1.0.4.jar to /home/cybuilder/cytoscape-admin-scripts/b

[INFO] Building zip: /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/gui-distribution/assembly/target/cytoscape-windows-3.7.2.zip
[INFO] 
[INFO] --- maven-install-plugin:2.3.1:install (default-install) @ cytoscape ---
[INFO] Installing /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/gui-distribution/assembly/pom.xml to /home/cybuilder/.m2/repository/org/cytoscape/distribution/cytoscape/3.7.2/cytoscape-3.7.2.pom
[INFO] Installing /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/gui-distribution/assembly/target/cytoscape-unix-3.7.2.tar.gz to /home/cybuilder/.m2/repository/org/cytoscape/distribution/cytoscape/3.7.2/cytoscape-3.7.2.tar.gz
[INFO] Installing /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/gui-distribution/assembly/target/cytoscape-windows-3.7.2.zip to /home/cybuilder/.m2/repository/org/cytoscape/distribution/cytoscape/3.7.2/cytoscape-3.7.2.zip
[INFO] 
[INFO] --- maven-deploy-plugin

[INFO] Installing /home/cybuilder/cytoscape-admin-scripts/build_3.7.2/cytoscape/cytoscape/pom.xml to /home/cybuilder/.m2/repository/org/cytoscape/project/3.7.2/project-3.7.2.pom
[INFO] 
[INFO] --- maven-deploy-plugin:2.7:deploy (default-deploy) @ project ---
[INFO] ------------------------------------------------------------------------
[INFO] Reactor Summary:
[INFO] 
[INFO] Basic Cytoscape POM Configuration ................. SUCCESS [1.739s]
[INFO] Cytoscape API Parent Project POM .................. SUCCESS [6.738s]
[INFO] Cytoscape Documentation Taglets ................... SUCCESS [2.996s]
[INFO] Cytoscape Event API (event-api) ................... SUCCESS [3.470s]
[INFO] Cytoscape Model API (model-api) ................... SUCCESS [4.547s]
[INFO] Cytoscape Service API (service-api) ............... SUCCESS [3.916s]
[INFO] Cytoscape View Model API (viewmodel-api) .......... SUCCESS [3.514s]
[INFO] Cytoscape CI API (ci-api) ......................... SUCCESS [2.667s]
[INFO] Cytoscape Work

[INFO] Final Memory: 144M/1503M
[INFO] ------------------------------------------------------------------------
[ERROR] Failed to execute goal org.apache.maven.plugins:maven-deploy-plugin:2.7:deploy (default-deploy) on project project: Deployment failed: repository element was not specified in the POM inside distributionManagement element or in -DaltDeploymentRepository=id::layout::url parameter -> [Help 1]
[ERROR] 
[ERROR] To see the full stack trace of the errors, re-run Maven with the -e switch.
[ERROR] Re-run Maven using the -X switch to enable full debug logging.
[ERROR] 
[ERROR] For more information about the errors and possible solutions, please read the following articles:
[ERROR] [Help 1] http://cwiki.apache.org/confluence/display/MAVEN/MojoExecutionException
[ERROR] 
[ERROR] After correcting the problems, you can resume the build with the command
[ERROR]   mvn <goals> -rf :project


## 8. Sign DMG and upload release to github

In [ ]:
cd(CYTOSCAPE_DIR, 'gui-distribution', 'packaging')
!./sign-dmg.sh && mv -f target/install4j/signed/*.dmg target/install4j/
!rmdir target/install4j/signed

#### Create a new release with Cytoscape installers: https://github.com/cytoscape/cytoscape/releases/new

## 9. Update Cytoscape.org, manual, and admin-scripts

Publish JavaDocs by building http://code.cytoscape.org/jenkins/job/cytoscape-3-javadoc/

Generate Release Notes from JIRA https://cytoscape.atlassian.net/projects/CYTOSCAPE

In [ ]:
# Update cytoscape.org

cd(BUILD_PARENT_DIR)
![[ -d cytoscape.github.com ]] || git clone http://github.com/cytoscape/cytoscape.github.com

![[ -d cytoscape-manual ]] || git clone http://github.com/cytoscape/cytoscape-manual

### Cytoscape.org changes

#### Roadmap
cytoscape.github.com/roadmap.html
- Remove section from Vision
- Move release dates 6-8 months forward
- Add section to Bottom of page listing features

#### JS Files:
- js/download.js
  - Copy JSON block to previous versions
- js/setup_page.js
  - Change release version
  
#### Welcome Letter
- Use template at cellar/users/bsettle/Documents/Cytoscape/Releases/
- Must update all sections

#### Release Notes
- releasenotes.html
  - Update welcome letter link
  - Update Latest Release Notes and Older Versions list
- release_notes_3_X_X.html
  - Copied from previous release notes
  - Edit HTML sections to add div's about new features
  - Add screenshots

In [ ]:
cd(BUILD_PARENT_DIR, 'cytoscape.github.com')
!git add .
!git commit -m "Updated for release {NEW_VERSION}"

### Manual
Refer to https://github.com/cytoscape/cytoscape-manual/ for manual changes and building

In [ ]:
#Change docs/conf.py
cd(BUILD_PARENT_DIR, 'cytoscape-manual', 'docs')
!ls conf.p* | xargs sed -i "" -e "s/{OLD_RELEASE_VERSION}/{NEW_VERSION}/g"
!git add .
!git commit -m "Updated for {NEW_VERSION} release"
!git push

- Update all sections with new features and screenshots
#### NOTE: ONLY TAG WHEN READY, Tagging posts the manual to ReadTheDocs
#### Only Major version updates are published. Not minor

Webhooks may be discontinued 1/31/2019. Keep an eye out for auto-building ReadTheDocs
To build it manually, you must have access to the ReadTheDocs page:
- https://readthedocs.org/projects/cytoscape-working-copy/

In [ ]:
cd(BUILD_PARENT_DIR, 'cytoscape-manual')
!git tag {NEW_VERSION}

### Update cytoscape-admin-scripts

In [ ]:
#system-checker files are in this repo
cd(BUILD_PARENT_DIR)
!ls system-checker/* | xargs sed -i "" -e "s/{OLD_RELEASE_VERSION}/{NEW_VERSION}/g"
!git add .
!git commit -m "Updated system checker"

### Publish the manual, website, and create a release on github
Check status before pushing!

In [ ]:
# Bump up the system checker scripts
cd(BUILD_PARENT_DIR)
!git status
#!git push

# Tag and publish Manual
cd(BUILD_PARENT_DIR, 'cytoscape-manual')
!git status
#!git push origin {NEW_VERSION}

# Update website
cd(BUILD_PARENT_DIR, 'cytoscape.github.com')
!git status
#!git push

### Update the file at /data/chianti/html/cytoscape-news/news.html

In [ ]:
!curl --silent http://chianti.ucsd.edu/cytoscape-news/news.html | grep "latestVersion"

### Announce the release on app-dev, cytoscape-announce, cytostaff

In [25]:
updates = [
    'Hotfix for a CyNDEx-2 bug where the JXBrowser component could not be downloaded'
]
update_list = '\n'.join([' - ' + update for update in updates])
welcome_letter = 'http://www.cytoscape.org/cy3_welcome_letter_v20.pdf'
release_notes = 'http://www.cytoscape.org/release_notes_3_7_2.html'
message = '''Cytoscape {version} is released!

=+=+ =+=+ =+=+ =+=+ =+=+ Hello Cytoscapers! =+=+ =+=+ =+=+ =+=+ =+=+
 
We're very pleased and excited to announce availability of Cytoscape {version}, effective immediately!

To get a copy, surf to http://cytoscape.org/download, and download and execute the installer for your workstation.

Here are the new features in {version}:
{update_list}

Note that with {version}, Windows & Mac systems can run Java 9 or 10 without conflicting with Cytoscape -- it installs and uses a private Java 8.

For Linux, you must be sure Java 8 is installed and is first on the PATH or is named via the JAVA_HOME environment variable.

If you find any issues with this release, please let us know by posting to cytoscape-helpdesk@googlegroups.com … we very much value your feedback!

Please check the {version} materials in our Welcome Letter ({welcome_letter}) and the Release Notes ({release_notes}).

Tell all your friends ...

We appreciate your checking this out, and we hope you find it as great to work with as we do!

=+=+ =+=+ =+=+ =+=+ =+=+ =+=+ =+=+ =+=+ =+=+ =+=+'''
print(message.format(version=NEW_VERSION, update_list=update_list, 
                     welcome_letter=welcome_letter, release_notes=release_notes))

Cytoscape 3.7.2 is released!

=+=+ =+=+ =+=+ =+=+ =+=+ Hello Cytoscapers! =+=+ =+=+ =+=+ =+=+ =+=+
 
We're very pleased and excited to announce availability of Cytoscape 3.7.2, effective immediately!

To get a copy, surf to http://cytoscape.org/download, and download and execute the installer for your workstation.

Here are the new features in 3.7.2:
 - Hotfix for a CyNDEx-2 bug where the JXBrowser component could not be downloaded

Note that with 3.7.2, Windows & Mac systems can run Java 9 or 10 without conflicting with Cytoscape -- it installs and uses a private Java 8.

For Linux, you must be sure Java 8 is installed and is first on the PATH or is named via the JAVA_HOME environment variable.

If you find any issues with this release, please let us know by posting to cytoscape-helpdesk@googlegroups.com … we very much value your feedback!

Please check the 3.7.2 materials in our Welcome Letter (http://www.cytoscape.org/cy3_welcome_letter_v20.pdf) and the Release Notes (http://www.cyt